In [ ]:
# %%
import pandas as pd
import numpy as np
import time
import plotly.graph_objects as go
import pickle
from statsforecast.utils import AirPassengersDF

from neuralforecast import NeuralForecast
from neuralforecast.models import MLP, NBEATS, NHITS, TFT,LSTM, TCN
from neuralforecast.auto import AutoMLP, AutoNBEATS, AutoNHITS, AutoTFT, AutoLSTM, AutoTCN
from neuralforecast.losses.pytorch import DistributionLoss, HuberMQLoss
from statsforecast.core import StatsForecast
from statsforecast.models import (
    Naive,
    SeasonalNaive,
    ARIMA,
    SimpleExponentialSmoothing,
    SimpleExponentialSmoothingOptimized,
    SeasonalExponentialSmoothing,
    SeasonalExponentialSmoothingOptimized,
    RandomWalkWithDrift,
    ETS,
    HistoricAverage,
    WindowAverage,
    AutoARIMA,
    AutoETS,
    AutoCES,
    AutoTheta
)
from tqdm.notebook import tqdm
from mlforecast import MLForecast
from xgboost import XGBRegressor
from catboost import CatBoostRegressor
from sklearn.ensemble import RandomForestRegressor
import lightgbm as lgb

from mlforecast.target_transforms import Differences
from mlforecast.lag_transforms import ExpandingMean, RollingMean
from numba import njit
from window_ops.rolling import rolling_mean
import ray
from ray import tune
# ray.init(log_to_driver=False)
from nixtla import NixtlaClient   # type: ignore
import contextlib
import io
# import warnings
# warnings.filterwarnings("ignore")
import logging
# logging.getLogger("lightning").setLevel(logging.ERROR)

# import logging

# # configure logging at the root level of Lightning
# logging.getLogger("lightning.pytorch").setLevel(logging.ERROR)
import pandas as pd

import numpy as np

desired_width=320

pd.set_option('display.width', desired_width)

np.set_printoptions(linewidth=desired_width)

pd.set_option('display.max_columns',10)
from chronos import ChronosPipeline
import torch
import os

if os.environ['CONDA_DEFAULT_ENV'] == 'torch':
    from gluonts.dataset.pandas import PandasDataset
    from gluonts.dataset.split import split
    from uni2ts.eval_util.plot import plot_single
    from uni2ts.model.moirai import MoiraiForecast, MoiraiModule
    from gluonts.dataset.util import to_pandas

In [2]:
def mase(y_true, y_pred, y_train):
    forecast_mae = np.mean(np.abs(y_true - y_pred))
    naive_forecast_diff = np.diff(np.trim_zeros(y_train))
    scale = np.mean(np.abs(naive_forecast_diff))
    mase = forecast_mae / scale
    return mase

def rmse(y_true, y_pred):
    return np.sqrt(np.mean((y_true - y_pred) ** 2))

def smape(y_true, y_pred):
    return np.mean(np.abs(y_pred - y_true) / ((np.abs(y_true) + np.abs(y_pred)) / 2))*100

def rmsse(y_true, y_pred, y_train):
    forecast_mse = np.mean((y_true - y_pred) ** 2)
    naive_forecast_diff = np.diff(np.trim_zeros(y_train))
    naive_forecast_mse = np.mean(naive_forecast_diff ** 2)
    rmsse_value = np.sqrt(forecast_mse / naive_forecast_mse)
    return rmsse_value

def smpe(y_true, y_pred):
    return 100 * np.mean((y_pred - y_true) / ((y_true + y_pred) / 2))

def ME(y_true, y_pred):
    return np.mean(y_true - y_pred)

def MAE(y_true, y_pred):
    return np.mean(np.abs(y_true - y_pred))

# def calculate_errors(test, forecasts, train):
#     df = pd.DataFrame()
#     for col in forecasts.columns:
#         if col in ['ds', 'unique_id', 'Model Type','T+x']:
#             continue
#         y_true = test['y'].values
#         y_pred = forecasts[col].values
#         y_train = train['y'].values
#         for i in range(len(test)):
#             error_dict = {
#                 'RMSE': rmse(y_true[i], y_pred[i]),
#                 'SMAPE': smape(y_true[i], y_pred[i]),
#                 'RMSSE': rmsse(y_true[i], y_pred[i], y_train),
#                 'SMPE' : smpe(y_true[i], y_pred[i]),
#                 'ME': ME(y_true[i], y_pred[i]),
#                 'MAE': MAE(y_true[i], y_pred[i]),
#                 'MASE': mase(y_true[i], y_pred[i], y_train)
#             }
#          df = df.concat()
#         df = pd.concat([pd.DataFrame(error_dict, index=[col]), df])
#     return df
import pandas as pd

def calculate_errors(test, forecasts, train):
    # Initialize an empty DataFrame to store the results
    df = pd.DataFrame()

    for col in forecasts.columns:
        # Skip non-forecast columns
        if col in ['ds', 'unique_id', 'Model Type', 'T+x']:
            continue

        # Extract the relevant series
        y_true = test['y'].values
        y_pred = forecasts[col].values
        y_train = train['y'].values

        # Iterate over each time point in the test set
        for i in range(len(test)):
            # Calculate the error metrics for the current time point
            error_dict = {
                'RMSE': rmse(y_true[i], y_pred[i]),
                'SMAPE': smape(y_true[i], y_pred[i]),
                'RMSSE': rmsse(y_true[i:i+1], y_pred[i:i+1], y_train),  # Use a slice for RMSSE
                'SMPE' : smpe(y_true[i], y_pred[i]),
                'ME': ME(y_true[i], y_pred[i]),
                'MAE': MAE(y_true[i], y_pred[i]),
                'MASE': mase(y_true[i:i+1], y_pred[i:i+1], y_train)  # Use a slice for MASE
            }

            # Create a DataFrame for the current error metrics and append it
            error_df = pd.DataFrame(error_dict,  index=[col])
            df = pd.concat([df, error_df], ignore_index=True)
        df['T+x'] = forecasts['T+x']
    return df


df = pd.read_csv('accidental-deaths-in-usa-monthly.csv')
df['ds'] = pd.to_datetime(df.Month.values.astype('datetime64[M]'), format='%Y-%m') + pd.offsets.MonthEnd() 
df = df.rename(columns={'Accidental deaths in USA: monthly, 1973 ? 1978':'y'}).drop(columns='Month')
df['unique_id'] = 1.0

test_size_total = 24
train_size_total = len(df) - test_size_total
train_total, test_total = df[:train_size_total], df[train_size_total:]



In [3]:

# %%
@njit
def rolling_mean_12(x):
    return rolling_mean(x, window_size=12)

@njit
def rolling_mean_24(x):
    return rolling_mean(x, window_size=24)

def month_index(times):
    return times.month


In [ ]:

# %%
# Model definitions
statistical_models = [
    Naive(),
    SeasonalNaive(12),
    ARIMA(order=[12, 1, 0]),
    ARIMA(order=[0, 1, 1], seasonal_order=[0, 1, 1], season_length=12, alias='SARIMA'),
    SimpleExponentialSmoothing(alpha=0.28),
    ETS(model='AAA', season_length=12, alias='ETS AAA'),
    ETS(model='MAM', season_length=12, alias='ETS MAM'),
    ETS(model='MMM', season_length=12, alias='ETS MMM'),
    ETS(model='MMM', season_length=12, alias='ETS MMdM', damped=True),
    ETS(model='MAM', season_length=12, alias='ETS MAdM', damped=True),
    HistoricAverage(),
    # WindowAverage(window_size=6),
    AutoARIMA(max_p=12),
    AutoETS(season_length=12),
    AutoETS(season_length=12, damped=True, alias='Damped AutoETS'),
    AutoCES(season_length=12, alias='AutoCES'),
    AutoTheta(season_length=12),
    SimpleExponentialSmoothingOptimized(),
    SeasonalExponentialSmoothing(season_length=12, alpha=0.28),
    SeasonalExponentialSmoothingOptimized(season_length=12),
    RandomWalkWithDrift()
]

lgb_params = {'verbosity': -1, 'num_leaves': 512}
catboost_params = {'subsample': 0.6, 'iterations': 50, 'depth': 5, 'verbose': 0}
xgboost_params = {'verbosity': 0, 'max_depth': 5, 'subsample': 0.6}
randomforest_params = {'verbose': 0, 'max_depth': 5}

tree_models = [
    [{'LightGBM': lgb.LGBMRegressor(**lgb_params)}],
    [{'CatBoost': CatBoostRegressor(**catboost_params)}],
    [{'XgBoost': XGBRegressor(**xgboost_params)}],
    [{'RandomForest': RandomForestRegressor(**randomforest_params)}],
]

neural_models_template = [
    MLP(input_size=2 * test_size_total, h=test_size_total,max_steps=100),
    NBEATS(input_size=2 * test_size_total, h=test_size_total,max_steps=100),
    NHITS(input_size=2 * test_size_total, h=test_size_total,max_steps=100),
    TFT(input_size=-1,h=test_size_total, max_steps=100,),
    LSTM(input_size=-1, h=test_size_total , max_steps=100),
    TCN(input_size=-1, h=test_size_total , max_steps=100),
    AutoMLP(config=dict(max_steps=100,input_size=tune.choice([3 * test_size_total]), learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1,verbose=False),
    AutoNBEATS(config=dict(max_steps=100, input_size=tune.choice([3 * test_size_total]), learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1, ),
    AutoNHITS(config=dict(max_steps=100,input_size=tune.choice([3 * test_size_total]), learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1, ),
    AutoTFT( h=test_size_total, num_samples=1,),
    AutoLSTM(h=test_size_total, num_samples=1,),
    AutoTCN(h=test_size_total, num_samples=1,)
]

from nixtla import NixtlaClient
nixtla_client = NixtlaClient(
    api_key = 'nixtla-tok-zoyazThf4YTdozZibXcWafdEFrmubwtGIcFuidUK8XYlkzYGQpU5tqLx9OWwevagReeN8fICeSgnMuH9'
)

morai_models = ['small', 'base', 'large']

chronos_models = ['tiny','mini','small','base','large']

In [5]:
forecast_horizons = [i for i in range(1,19)]
# forecast_horizons = [18, 12, 1]

def log_to_file(message):
    with open("model_training_log.txt", "a") as file:
        file.write(message + "\n")


def train_and_predict_statistical(model, train, horizon):
    sf = StatsForecast(models=[model], freq='ME', n_jobs=-1)
    start_time = time.time()
    forecasts_df = sf.forecast(df=train, h=horizon,fitted=True)
    train_time = time.time() - start_time
    insample_forecast_df = sf.forecast_fitted_values()
    return forecasts_df, train_time, insample_forecast_df

def train_and_predict_tree(model, train, horizon):
    fcst = MLForecast(
        models=model[0],
        freq="ME",
        target_transforms=[Differences([12])],
        lags=[1, 2, 3, 4, 11, 12, 18],
        lag_transforms={1: [ExpandingMean()], 12: [RollingMean(window_size=12)]}, # type: ignore
        date_features=[month_index]
    )
    model_tree = list(model[0])
    start_time = time.time()
    fcst.fit(train)
    forecasts_df = fcst.predict(h=horizon)
    train_time = time.time() - start_time
    # insample_forecast_df = fcst.forecast_fitted_values()
    return forecasts_df, train_time, model_tree

def train_and_predict_neural(model, train, horizon):
    nf = NeuralForecast(models=[model], freq='ME')
    start_time = time.time()
    
    val_size = 19 if horizon > 12 else 12

    nf.fit(df=train, verbose=False, val_size=val_size)
    forecasts_df = nf.predict(verbose=False)
    train_time = time.time() - start_time
    # insample_forecast_df = nf.predict_insample(step_size=horizon)
    return forecasts_df, train_time

def train_and_predict_moirai(model, train, horizon):
    SIZE = model # model size: choose from {'small', 'base', 'large'}
    PDT = horizon  # prediction length: any positive integer
    CTX = len(train)  # context length: any positive integer
    train = train.set_index('ds').drop(columns='unique_id')
    ds = PandasDataset(train, target="y", freq='M')
    # Prepare pre-trained model by downloading model weights from huggingface hub
    model = MoiraiForecast(
        module=MoiraiModule.from_pretrained(f"Salesforce/moirai-1.1-R-{SIZE}"),
        prediction_length=PDT,
        context_length=CTX,
        target_dim=1,
        feat_dynamic_real_dim=ds.num_feat_dynamic_real,
        past_feat_dynamic_real_dim=ds.num_past_feat_dynamic_real,
    )
    start_time = time.time()
    predictor = model.create_predictor(batch_size=32)
    forecasts = predictor.predict(ds)
    forecast_it = iter(forecasts)
    forecast = next(forecast_it)
    train_time = time.time() - start_time
    forecasts_df = pd.DataFrame(forecast.mean_ts).rename(columns={0:f'Moirai_{SIZE}'})  # type: ignore
    forecasts_df = forecasts_df.reset_index().rename(columns={'index':'ds'})
    forecasts_df['ds'] = pd.to_datetime(forecasts_df.ds.values.astype('datetime64[M]'), format='%Y-%m') + pd.offsets.MonthEnd() # type: ignore
    
    return forecasts_df, train_time
    

def train_and_predict_timegpt(train, horizon):
    start_time = time.time()
    model_version = 'timegpt-1-long-horizon' if horizon > 12 else 'timegpt-1'
    forecasts_df = nixtla_client.forecast(df=train, h=horizon, freq='M', time_col='ds', target_col='y', model=model_version)
    train_time = time.time() - start_time
    # forecasts_df = df.tail(horizon)
    # insample_forecast_df = df.iloc[:-horizon]
    return forecasts_df, train_time

def train_and_predict_chronos(model, train, horizon):
    # Prepare pre-trained model by downloading model weights from huggingface hub
    start_time = time.time()
    pipeline = ChronosPipeline.from_pretrained(
        f"amazon/chronos-t5-{model}",
        device_map="cuda",
        torch_dtype=torch.bfloat16,
    )
    forecast = pipeline.predict(
        context=torch.tensor(train["y"]),
        prediction_length=horizon,
        num_samples=1,
    )
    train_time = time.time() - start_time
    last_index = train.ds[-1:].values[0]
    date_range = pd.date_range(start=last_index, periods=horizon+1,freq='ME',inclusive='neither')
    forecasts_df = pd.DataFrame(forecast[0][0],index=date_range).rename(columns={0:f'Chronos_{model}'})  # type: ignore
    forecasts_df = forecasts_df.reset_index().rename(columns={'index':'ds'})
    
    return forecasts_df, train_time

def forecast_and_evaluate_overlapping(models, model_type, forecast_horizons, train_total, test_total, df):
    errors_by_horizon = {horizon: [] for horizon in forecast_horizons}
    forecasts_by_horizon = {horizon: [] for horizon in forecast_horizons}
    
    insample_forecasts_by_horizon = {horizon: [] for horizon in forecast_horizons}

    for horizon in tqdm(forecast_horizons, desc='Horizon Progress'):
        if model_type == 'neural':
            input_size = (2*horizon) if (2*horizon) > 12 else 12
            
            if horizon != 1:
                default_config_AutoNBEATS=AutoNBEATS(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoNBEATS.update({'early_stop_patience_steps':3, 'val_check_steps':10, 'start_padding_enabled':True, 'input_size': tune.choice([input_size]) })

                default_config_AutoNHITS=AutoNHITS(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoNHITS.update({'early_stop_patience_steps':3, 'val_check_steps':10, 'start_padding_enabled':True , 'input_size': tune.choice([input_size])})

                default_config_AutoTFT=AutoTFT(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoTFT.update({'early_stop_patience_steps':3, 'val_check_steps':10, 'start_padding_enabled':True , 'input_size': tune.choice([input_size])})

                default_config_AutoMLP=AutoMLP(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoMLP.update({ 'early_stop_patience_steps':3, 'val_check_steps':10, 'start_padding_enabled':True, 'input_size': tune.choice([input_size])})
                
                default_config_AutoLSTM=AutoLSTM(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoLSTM.update({ 'early_stop_patience_steps':3, 'val_check_steps':10, 'input_size': tune.choice([input_size])})
                
                default_config_AutoTCN=AutoTCN(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoTCN.update({ 'early_stop_patience_steps':3, 'val_check_steps':10, 'input_size': tune.choice([input_size])})
                
                models = [
                    MLP(input_size=input_size, h=horizon, max_steps=500,  early_stop_patience_steps=3, val_check_steps=10,start_padding_enabled=True ),
                    NBEATS(input_size=input_size, h=horizon, max_steps=500,  early_stop_patience_steps=3, val_check_steps=10 ,start_padding_enabled=True ),
                    NHITS(input_size=input_size, h=horizon, max_steps=500, early_stop_patience_steps=3, val_check_steps=10 ,start_padding_enabled=True ),
                    TFT(input_size = input_size , h=horizon, max_steps=500, early_stop_patience_steps=3, val_check_steps=10 ,start_padding_enabled=True ),
                    LSTM(input_size= -1, h=horizon , max_steps=500 ,early_stop_patience_steps=3, val_check_steps=10 ),
                    TCN(input_size=-1, h=horizon , max_steps=500, early_stop_patience_steps=3, val_check_steps=10 ),
                    # AutoMLP( config = default_config_AutoMLP, h=horizon,),
                    # AutoNBEATS(config = default_config_AutoNBEATS, h=horizon,),
                    # AutoNHITS(config = default_config_AutoNHITS, h=horizon,),
                    # AutoTFT(config = default_config_AutoTFT, h=horizon,),
                    # AutoLSTM(config = default_config_AutoLSTM, h=horizon,),
                    # AutoTCN(config = default_config_AutoTCN, h=horizon,),
                ]
            elif horizon == 1:
                default_config_AutoNBEATS=AutoNBEATS(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoNBEATS.update({'stack_types':['identity'], 'early_stop_patience_steps':3, 'val_check_steps':10, 'start_padding_enabled':True, 'input_size': tune.choice([input_size])})

                default_config_AutoNHITS=AutoNHITS(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoNHITS.update({'stack_types':['identity'], 'early_stop_patience_steps':3, 'val_check_steps':10, 'start_padding_enabled':True, 'input_size': tune.choice([input_size])})

                default_config_AutoTFT=AutoTFT(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoTFT.update({'early_stop_patience_steps':3, 'val_check_steps':10,'start_padding_enabled':True, 'input_size': tune.choice([input_size])})

                default_config_AutoMLP=AutoMLP(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoMLP.update({ 'early_stop_patience_steps':3, 'val_check_steps':10,'start_padding_enabled':True, 'input_size': tune.choice([input_size])})
                
                default_config_AutoLSTM=AutoLSTM(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoLSTM.update({ 'early_stop_patience_steps':3, 'val_check_steps':10, 'input_size': tune.choice([input_size])})
                
                default_config_AutoTCN=AutoTCN(h=horizon).get_default_config(h=horizon, backend='ray')
                default_config_AutoTCN.update({ 'early_stop_patience_steps':3, 'val_check_steps':10, 'input_size': tune.choice([input_size])})
                
                models = [
                    MLP(input_size=input_size, h=horizon, max_steps=500,  early_stop_patience_steps=3, val_check_steps=10,start_padding_enabled=True ),
                    NBEATS(input_size=input_size, h=horizon, max_steps=500,  stack_types = ["identity"],early_stop_patience_steps=3, val_check_steps=10,start_padding_enabled=True ),
                    NHITS(input_size=input_size, h=horizon, max_steps=500,  stack_types = ["identity"],early_stop_patience_steps=3, val_check_steps=10,start_padding_enabled=True ),
                    TFT(input_size= input_size, h=horizon, max_steps=500, early_stop_patience_steps=3, val_check_steps=10,start_padding_enabled=True ),
                    LSTM(input_size= -1, h=horizon , max_steps=500 ,early_stop_patience_steps=3, val_check_steps=10),
                    TCN(input_size=-1, h=horizon , max_steps=500, early_stop_patience_steps=3, val_check_steps=10),
                    # AutoMLP( config = default_config_AutoMLP, h=horizon,),
                    # AutoNBEATS(config = default_config_AutoNBEATS, h=horizon,),
                    # AutoNHITS(config = default_config_AutoNHITS, h=horizon,),
                    # AutoTFT(config = default_config_AutoTFT, h=horizon,),
                    # AutoLSTM(config = default_config_AutoLSTM, h=horizon,),
                    # AutoTCN(config = default_config_AutoTCN, h=horizon,),
                           ]
        
        for model in tqdm(models, desc=f'Model Progress for Horizon {horizon}'):
            total_train_time = 0
            combined_forecasts = pd.DataFrame()
            combined_error = pd.DataFrame()
            
            combined_insample_forecasts = pd.DataFrame()
            combined_insample_error = pd.DataFrame()

            for start in range(0, test_size_total):
                if train_size_total + start + horizon > train_size_total + test_size_total:
                    break

                train_size = train_size_total + start
                train = df[:train_size]
                test = df[train_size:train_size + horizon]

                log_to_file(f'Air Passanger Horizon: {horizon} for {model} with origin {train_size} has started running at {time.ctime()}')
                # print(f'Horizon: {horizon} for {model} with origin {train_size} has started running at {time.ctime()}')
                
                insample_forecast_df = None
                
                if model_type == 'statistical':
                    forecasts_df, train_time, insample_forecast_df = train_and_predict_statistical(model, train, horizon)
                    forecasts_df['Model Type'] = 'Statistical'
                    
                elif model_type == 'tree':
                    forecasts_df, train_time, model_tree = train_and_predict_tree(model, train, horizon)
                    forecasts_df['Model Type'] = 'Tree'

                elif model_type == 'neural':
                    forecasts_df, train_time = train_and_predict_neural(model, train, horizon)
                    forecasts_df['Model Type'] = 'Neural'

                elif model_type == 'TimeGPT':
                    forecasts_df, train_time = train_and_predict_timegpt(train, horizon)
                    forecasts_df['Model Type'] = 'Foundational'
                    
                elif model_type == 'Moirai':
                    forecasts_df, train_time = train_and_predict_moirai(model,train, horizon)
                    forecasts_df['Model Type'] = 'Foundational'
                    
                elif model_type == 'Chronos':
                    forecasts_df, train_time = train_and_predict_chronos(model,train, horizon)
                    forecasts_df['Model Type'] = 'Foundational'

                forecasts_df['origin'] = train_size # type: ignore
                forecasts_df['horizon'] = horizon # type: ignore
                forecasts_df['T+x'] = list(range(1,horizon+1)) # type: ignore
                
                if insample_forecast_df is not None:
                    insample_forecast_df['origin'] = train_size # type: ignore
                    insample_forecast_df['horizon'] = horizon # type: ignore
                    insample_forecast_df['T+x'] = list(range(1,len(insample_forecast_df)+1)) # type: ignore
                    combined_insample_forecasts = pd.concat([combined_insample_forecasts, insample_forecast_df]) # type: ignore
                else: 
                    combined_insample_forecasts = None
                    
                    
                combined_forecasts = pd.concat([combined_forecasts, forecasts_df]) # type: ignore
                error_df = calculate_errors(test, forecasts_df.drop(columns=['origin', 'horizon']), train) # type: ignore
                error_df['origin'] = train_size
                # error_df['origin'] = train_size
                error_df['horizon'] = horizon
                error_df['train_time'] = train_time
                error_df['Model Type'] = forecasts_df['Model Type']

                combined_error = pd.concat([combined_error, error_df])
                total_train_time += train_time
                
            combined_forecasts = combined_forecasts.groupby('ds').mean(numeric_only=True).reset_index()
            
            combined_error['Total_Train_Time'] = total_train_time
            if model_type == 'tree': 
                model_name = model_tree[0] 
            elif model_type == 'Chronos':
                model_name =  f'Chronos_{model}'
            elif model_type == 'Moirai':
                model_name =  f'Moirai_{model}'
            else:
                model_name = str(model)
            combined_forecasts['Model'] = model_name
            combined_error['Model'] = model_name
            
            if combined_insample_forecasts is not None:
                combined_insample_forecasts['Model'] = model_name
                insample_forecasts_by_horizon[horizon].append(combined_insample_forecasts)
                
                
            forecasts_by_horizon[horizon].append(combined_forecasts)
            errors_by_horizon[horizon].append(combined_error)

        with open('errors.pickle', 'wb') as handle:
            pickle.dump(errors_by_horizon, handle, protocol=pickle.HIGHEST_PROTOCOL)

        with open('forecasts_by_horizon.pickle', 'wb') as handle:
            pickle.dump(forecasts_by_horizon, handle, protocol=pickle.HIGHEST_PROTOCOL)

    return errors_by_horizon, forecasts_by_horizon, combined_insample_forecasts


In [6]:
# # Forecast and evaluate neural models
# neural_errors_accidental_deaths, neural_forecasts_by_horizon_accidental_deaths, neural_insample_forecasts_by_horizon_accidental_deaths = forecast_and_evaluate_overlapping(neural_models_template, 'neural', forecast_horizons, train_total, test_total, df) # type: ignore

# with open('neural_errors_accidental_deaths.pickle', 'wb') as handle:
#     pickle.dump(neural_errors_accidental_deaths, handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('neural_forecasts_by_horizon_accidental_deaths.pickle', 'wb') as handle:  
#     pickle.dump(neural_forecasts_by_horizon_accidental_deaths, handle, protocol=pickle.HIGHEST_PROTOCOL)

  
with open('neural_forecasts_by_horizon_accidental_deaths.pickle', 'rb') as handle:
    neural_forecasts_by_horizon_accidental_deaths = pickle.load(handle)
    
    
with open('neural_errors_accidental_deaths.pickle', 'rb') as handle:
    neural_errors_accidental_deaths = pickle.load(handle)    

In [7]:
# Forecast and evaluate tree-based models
# tree_errors_accidental_deaths , tree_forecasts_by_horizon_accidental_deaths, tree_insample_forecasts_by_horizon  = forecast_and_evaluate_overlapping(tree_models, 'tree', forecast_horizons, train_total, test_total, df)
# with open('tree_errors_accidental_deaths.pickle', 'wb') as handle:
#     pickle.dump(tree_errors_accidental_deaths, handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('tree_forecasts_by_horizon_accidental_deaths.pickle', 'wb') as handle:
#     pickle.dump(tree_forecasts_by_horizon_accidental_deaths, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
    
with open('tree_forecasts_by_horizon_accidental_deaths.pickle', 'rb') as handle:
    tree_forecasts_by_horizon_accidental_deaths = pickle.load(handle)
    
    
with open('tree_errors_accidental_deaths.pickle', 'rb') as handle:
    tree_errors_accidental_deaths = pickle.load(handle) 

In [8]:
# chronos_errors_accidental_deaths , chronos_forecasts_by_horizon_accidental_deaths, chronos_insample_forecasts_by_horizon_accidental_deaths = forecast_and_evaluate_overlapping(chronos_models, 'Chronos', forecast_horizons, train_total, test_total, df)
# with open('chronos_errors_accidental_deaths.pickle', 'wb') as handle:
#     pickle.dump(chronos_errors_accidental_deaths, handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('chronos_forecasts_by_horizon_accidental_deaths.pickle', 'wb') as handle:
#     pickle.dump(chronos_forecasts_by_horizon_accidental_deaths, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
    
with open('chronos_forecasts_by_horizon_accidental_deaths.pickle', 'rb') as handle:
    chronos_forecasts_by_horizon_accidental_deaths = pickle.load(handle)
    
    
with open('chronos_errors_accidental_deaths.pickle', 'rb') as handle:
    chronos_errors_accidental_deaths = pickle.load(handle) 

In [9]:
# morai_errors_accidental_deaths , morai_forecasts_by_horizon_accidental_deaths, morai_insample_forecasts_by_horizon_accidental_deaths  = forecast_and_evaluate_overlapping(morai_models, 'Moirai', forecast_horizons, train_total, test_total, df)

# with open('morai_errors_accidental_deaths .pickle', 'wb') as handle:
#     pickle.dump(morai_errors_accidental_deaths , handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('morai_forecasts_by_horizon_accidental_deaths .pickle', 'wb') as handle:  
#     pickle.dump(morai_forecasts_by_horizon_accidental_deaths , handle, protocol=pickle.HIGHEST_PROTOCOL)

  
with open('morai_forecasts_by_horizon_accidental_deaths .pickle', 'rb') as handle:
    morai_forecasts_by_horizon_accidental_deaths  = pickle.load(handle)
    
    
with open('morai_errors_accidental_deaths .pickle', 'rb') as handle:
    morai_errors_accidental_deaths  = pickle.load(handle)    

In [10]:
# # # Forecast and evaluate statistical models
# statistical_errors_accidental_deaths , statistical_forecasts_by_horizon_accidental_deaths , statistical_insample_forecasts_by_horizon_accidental_deaths  = forecast_and_evaluate_overlapping(statistical_models, 'statistical', forecast_horizons, train_total, test_total, df)
# with open('statistical_errors_accidental_deaths .pickle', 'wb') as handle:
#     pickle.dump(statistical_errors_accidental_deaths , handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('statistical_forecasts_by_horizon_accidental_deaths .pickle', 'wb') as handle:
#     pickle.dump(statistical_forecasts_by_horizon_accidental_deaths , handle, protocol=pickle.HIGHEST_PROTOCOL)


with open('statistical_forecasts_by_horizon_accidental_deaths .pickle', 'rb') as handle:
    statistical_forecasts_by_horizon_accidental_deaths  = pickle.load(handle)
    
    
with open('statistical_errors_accidental_deaths .pickle', 'rb') as handle:
    statistical_errors_accidental_deaths  = pickle.load(handle)

In [11]:
# TimeGPT_errors_accidental_deaths , TimeGPT_forecasts_by_horizon_accidental_deaths , TimeGPT_insample_forecasts_by_horizon_accidental_deaths   = forecast_and_evaluate_overlapping(['TimeGPT'], 'TimeGPT', forecast_horizons, train_total, test_total, df)
# with open('TimeGPT_errors_accidental_deaths .pickle', 'wb') as handle:
#     pickle.dump(TimeGPT_errors_accidental_deaths , handle, protocol=pickle.HIGHEST_PROTOCOL)

# with open('TimeGPT_forecasts_by_horizon_accidental_deaths .pickle', 'wb') as handle:
#     pickle.dump(TimeGPT_forecasts_by_horizon_accidental_deaths , handle, protocol=pickle.HIGHEST_PROTOCOL)
    
    
with open('TimeGPT_forecasts_by_horizon_accidental_deaths .pickle', 'rb') as handle:
    TimeGPT_forecasts_by_horizon_accidental_deaths  = pickle.load(handle)
    
    
with open('TimeGPT_errors_accidental_deaths .pickle', 'rb') as handle:
    TimeGPT_errors_accidental_deaths  = pickle.load(handle)

In [12]:
# %%
# Plot all forecasts combined
import plotly.graph_objects as go

def plot_all_forecasts(df, forecasts_by_horizon, model_type):
    fig = go.Figure()

    # Add actual data
    fig.add_trace(go.Scatter(x=df['ds'], y=df['y'], mode='lines', name='Actual'))

    # Add forecasts
    for horizon, forecasts_list in forecasts_by_horizon.items():
        combined_forecasts = pd.concat(forecasts_list).reset_index(drop=True)
        for col in combined_forecasts.columns:
            if col in ['ds', 'unique_id', 'origin','horizon','Model','index']:
                continue
            fig.add_trace(go.Scatter(x=combined_forecasts['ds'], y=combined_forecasts[col], mode='lines', name=f'{col} (Horizon {horizon})'))

    fig.update_layout(title=f'All Forecasts by Horizon ({model_type})', xaxis_title='Date', yaxis_title='Passengers')
    fig.show()

In [ ]:
# # Plot forecasts for statistical models
plot_all_forecasts(df, statistical_forecasts_by_horizon_accidental_deaths , 'statistical')

# # Plot forecasts for tree-based models
plot_all_forecasts(df, tree_forecasts_by_horizon_accidental_deaths , 'tree')

# # Plot forecasts for neural models
plot_all_forecasts(df, neural_forecasts_by_horizon_accidental_deaths , 'neural')

# # Plot forecasts for Morai
plot_all_forecasts(df, morai_forecasts_by_horizon_accidental_deaths , 'Moirai')

# # Plot forecasts for Chronos
plot_all_forecasts(df, chronos_forecasts_by_horizon_accidental_deaths , 'Chronos')

# # Plot forecasts for TimeGPT
plot_all_forecasts(df, TimeGPT_forecasts_by_horizon_accidental_deaths , 'TimeGPT')

# %%
# Plot forecasts separately by horizon
def plot_forecasts_by_horizon(df, forecasts_by_horizon, model_type):
    for horizon, forecasts_list in forecasts_by_horizon.items():
        fig = go.Figure()
        # Add actual data
        fig.add_trace(go.Scatter(x=df['ds'], y=df['y'], mode='lines', name='Actual'))

        # Add forecasts for the current horizon
        combined_forecasts = pd.concat(forecasts_list).reset_index(drop=True)
        for col in combined_forecasts.columns:
            if col in ['ds', 'unique_id', 'origin','horizon','Model','index']:
                continue
            fig.add_trace(go.Scatter(x=combined_forecasts['ds'], y=combined_forecasts[col], mode='lines', name=f'{col} (Horizon {horizon})'))

        fig.update_layout(title=f'Forecasts for Horizon {horizon} ({model_type})', xaxis_title='Date', yaxis_title='Passengers')
        fig.show()

# # Plot forecasts for statistical models by horizon
# plot_forecasts_by_horizon(df, statistical_forecasts_by_horizon, 'statistical')

# # Plot forecasts for tree-based models by horizon
# plot_forecasts_by_horizon(df, tree_forecasts_by_horizon, 'tree')

# # Plot forecasts for neural models by horizon
# plot_forecasts_by_horizon(df, neural_forecasts_by_horizon, 'neural')

# # Plot forecasts for TimeGPT by horizon
# plot_forecasts_by_horizon(df, TimeGPT_forecasts_by_horizon, 'TimeGPT')


In [14]:
# Collect and combine all errors from different horizons into a single DataFrame
def combine_errors(errors_by_horizon):
    combined_errors = []
    for horizon, errors_list in errors_by_horizon.items():
        for error_df in errors_list:
            error_df['Horizon'] = horizon
            combined_errors.append(error_df)
    combined_errors_df = pd.concat(combined_errors, ignore_index=True)
    return combined_errors_df

# all_errors_neural = combine_errors(neural_errors)
# all_errors = pd.concat([combine_errors(tree_errors), combine_errors(statistical_errors) combine_errors(TimeGPT_errors),combine_errors(neural_errors)], ignore_index=True)
# all_errors = pd.concat([combine_errors(tree_errors), combine_errors(statistical_errors), combine_errors(TimeGPT_errors), combine_errors(chronos_errors), combine_errors(morai_errors)], ignore_index=True)

all_errors_accidental_deaths = pd.concat([combine_errors(tree_errors_accidental_deaths ), combine_errors(statistical_errors_accidental_deaths ), 
                        combine_errors(TimeGPT_errors_accidental_deaths ), combine_errors(chronos_errors_accidental_deaths ),
                        combine_errors(neural_errors_accidental_deaths ), combine_errors(morai_errors_accidental_deaths )], ignore_index=True)

# all_errors_accidental_deaths = pd.concat([combine_errors(tree_errors_accidental_deaths ), combine_errors(statistical_errors_accidental_deaths ), 
#                         combine_errors(TimeGPT_errors_accidental_deaths ), combine_errors(chronos_errors_accidental_deaths ),
#                         combine_errors(neural_errors_accidental_deaths )], ignore_index=True)

# all_errors = pd.concat([combine_errors(tree_errors),combine_errors(chronos_errors),], ignore_index=True)


all_errors_accidental_deaths['avg_train_time'] = all_errors_accidental_deaths['train_time']
all_errors_accidental_deaths['sum_count'] = 1

# Add other error combinations if needed
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
all_errors_subset_accidental_deaths = all_errors_accidental_deaths[all_errors_accidental_deaths.Horizon == all_errors_accidental_deaths['T+x']]

In [15]:
# Aggregating metrics across models and time steps (mean and std)
all_errors_per_time_step_accidental_deaths = all_errors_subset_accidental_deaths.groupby(['Model', 'T+x']).agg({
    'RMSE': 'mean',
    'SMAPE': 'mean',
    'RMSSE': 'mean',
    'SMPE': 'mean',
    'ME': 'mean',
    'MAE': 'mean',
    'MASE': 'mean',
    'train_time': 'sum',
    'sum_count': 'sum',
    'avg_train_time': 'mean',
    'Model Type': 'first'
}).reset_index()

# Calculate the standard deviation for the metrics
all_errors_per_time_step_std_accidental_deaths = all_errors_subset_accidental_deaths.groupby(['Model', 'T+x']).agg({
    'RMSE': 'std',
    'SMAPE': 'std',
    'RMSSE': 'std',
    'SMPE': 'std',
    'ME': 'std',
    'MAE': 'std',
    'MASE': 'std'
}).reset_index()

# Merge the mean and std dataframes
all_errors_per_time_step_accidental_deaths = pd.merge(
    all_errors_per_time_step_accidental_deaths, 
    all_errors_per_time_step_std_accidental_deaths, 
    on=['T+x', 'Model'], 
    suffixes=('', '_std')
)
all_errors_per_time_step_accidental_deaths['Model'] = all_errors_per_time_step_accidental_deaths['Model'].str.replace('_', ' ')
all_errors_per_time_step_accidental_deaths.to_csv('results/all_errors_per_time_step_accidental_deaths.csv')


In [21]:
all_errors_accidental_deaths.to_csv('all_errors_accidental_deaths.csv')

In [22]:
color_map = {
'Statistical': '#636EFA',  # Blue
'Foundational': '#EF553B',  # Red
'Tree': '#00CC96',  # Green
'Neural': '#AB63FA'  # Purple
}

In [ ]:
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd


def create_sorted_bar_plot(data, x, y, title, color, text=None, color_map=None, sort_by_abs=False):
    # Sort data by absolute value if required
    color_map = {
    'Statistical': '#636EFA',  # Blue
    'Foundational': '#EF553B',  # Red
    'Tree': '#00CC96',  # Green
    'Neural': '#AB63FA'  # Purple
    }
    if sort_by_abs:
        sorted_data = data.reindex(data[y].abs().sort_values().index)
    else:
        sorted_data = data.sort_values(by=y)
    
    fig = go.Figure()

    unique_model_types = sorted_data[color].unique()
    
    if color_map is None:
        # Generate a default color map if none is provided
        color_map = {model_type: px.colors.qualitative.Plotly[i % len(px.colors.qualitative.Plotly)] 
                     for i, model_type in enumerate(unique_model_types)}
    
    for model_type in unique_model_types:
        df_type = sorted_data[sorted_data[color] == model_type]
        fig.add_trace(go.Bar(
            x=df_type[x],
            y=df_type[y],
            name=model_type,
            text=df_type[text] if text else None,
            textposition='outside',
            marker_color=color_map[model_type]
        ))
    
    fig.update_layout(
        title=title,
        xaxis_title=x,
        yaxis_title=y,
        legend_title=color,
        font=dict(size=10),
        xaxis_tickangle=-45,
        barmode='group',
        plot_bgcolor='white',
        xaxis=dict(showgrid=True, gridcolor='lightgray'),
        yaxis=dict(showgrid=True, gridcolor='lightgray')
    )
    
    fig.update_xaxes(categoryorder='array', categoryarray=sorted_data[x])
    
    return fig

def create_scatter_plot(data, metric, naive_performance, title):
    data['Average Training Time'] = data['avg_train_time']
    fig = px.scatter(data, x=metric, y='Average Training Time', color='Model Type', title=title, text='Model',
                     opacity=0.8, size_max=10, log_x=True, log_y=True)
    
    fig.add_trace(
        go.Scatter(
            x=[naive_performance[0], naive_performance[0]],
            y=[data['Average Training Time'].min(), data['Average Training Time'].max()],
            mode='lines',
            name='Seasonal Naive Performance',
            line=dict(color='red', width=2, dash='dash')
        )
    )
    
    fig.update_traces(
        marker=dict(size=15),  
        textposition='top right',  
        textfont=dict(family="sans serif", size=12, color="black"),
        selector=dict(mode='markers+text')
    )
    
    fig.update_layout(
        autosize=False,
        width=1600,
        height=800,
        margin=dict(l=40, r=40, b=40, t=40),
        plot_bgcolor='white',
        xaxis=dict(showgrid=True, gridcolor='lightgray'),
        yaxis=dict(showgrid=True, gridcolor='lightgray')
    )
    
    return fig

def create_aggregated_plots(error_metric, bias_metric, all_errors_per_time_step, short_time_step_range, medium_time_step_range, long_time_step_range):
    ranges = {
        'Short-term': short_time_step_range,
        'Medium-term': medium_time_step_range,
        'Long-term': long_time_step_range
    }
    
    for time_step_label, time_step_range in ranges.items():
        data_filtered = all_errors_per_time_step[(all_errors_per_time_step['T+x'] >= time_step_range[0]) & (all_errors_per_time_step['T+x'] <= time_step_range[1])]
        
        if data_filtered.empty:
            print(f"No data for {time_step_label} time step range {time_step_range}")
            continue

        data_agg = data_filtered.groupby('Model').agg({
            'RMSE': 'mean', 'SMAPE': 'mean', 'RMSSE': 'mean', 'SMPE': 'mean',
            'ME': 'mean', 'MAE': 'mean', 'MASE': 'mean',
            'train_time': 'sum', 'avg_train_time': 'mean', 'Model Type': 'first'
        }).reset_index()
        
        data_agg_std = data_filtered.groupby('Model').agg({
            'RMSE': 'std', 'SMAPE': 'std', 'RMSSE': 'std', 'SMPE': 'std',
            'ME': 'std', 'MAE': 'std', 'MASE': 'std'
        }).reset_index()
        
        data_agg = pd.merge(data_agg, data_agg_std, on='Model', suffixes=('', '_std'))

        best_models = data_agg.loc[data_agg.groupby('Model')[error_metric].idxmin()]

        fig_min_errors = create_sorted_bar_plot(best_models, 'Model', error_metric, 
                                                f'Minimum {error_metric} by Model ({time_step_label} time step)', 
                                                'Model Type', 'Model',)
        fig_min_errors.show()
        
        fig_min_bias = create_sorted_bar_plot(best_models, 'Model', bias_metric, 
                                              f'Minimum {bias_metric} by Model ({time_step_label} time step)', 
                                              'Model Type', 'Model',sort_by_abs=True)
        fig_min_bias.show()

        fig_train_times = create_sorted_bar_plot(data_agg, 'Model', 'train_time', 
                                                 f'Total Training Times by Model ({time_step_label} time step)', 
                                                 'Model Type',)
        fig_train_times.update_yaxes(type="log")
        fig_train_times.show()
        
        fig_train_times_avg = create_sorted_bar_plot(data_agg, 'Model', 'avg_train_time', 
                                                     f'Avg Training Times by Model ({time_step_label} time step)', 
                                                     'Model Type',)
        fig_train_times_avg.update_yaxes(type="log")
        fig_train_times_avg.show()

        fig_box_plot_error = px.box(data_filtered, x='Model', y=error_metric, 
                                    title=f'Box Plot of {error_metric} by Model ({time_step_label} time step)', 
                                    color='Model Type', color_discrete_map=color_map)
        fig_box_plot_error.update_layout(plot_bgcolor='white', xaxis=dict(showgrid=True, gridcolor='lightgray'), 
                                         yaxis=dict(showgrid=True, gridcolor='lightgray'))
        fig_box_plot_error.update_xaxes(categoryorder='mean ascending', categoryarray=data_filtered.groupby('Model')[error_metric].mean().sort_values().index)
        fig_box_plot_error.show()
        
        
        fig_box_plot_bias = px.box(data_filtered, x='Model', y=bias_metric, title=f'Box Plot of {bias_metric} by Model', color='Model Type')
        fig_box_plot_bias.update_layout(
        plot_bgcolor='white', 
        xaxis=dict(showgrid=True, gridcolor='lightgray'), 
        yaxis=dict(showgrid=True, gridcolor='lightgray'))
        sorted_models = abs(data_filtered.groupby('Model')[bias_metric].mean()).sort_values().index
        fig_box_plot_bias.update_xaxes( categoryorder='array', categoryarray=sorted_models)
        fig_box_plot_bias.show()

        

        naive_performance = data_agg[data_agg.Model == 'Naive'][error_metric].values  
        fig_scatter = create_scatter_plot(data_agg, error_metric, naive_performance, 
                                          f'Train Time vs {error_metric} ({time_step_label} time step)')
        fig_scatter.show()

def create_aggregated_plots_total(error_metric, bias_metric, all_errors_per_time_step):
    best_models = all_errors_per_time_step.loc[all_errors_per_time_step.groupby('T+x')[error_metric].idxmin()]

    fig_min_errors_time_step = px.bar(best_models, x='T+x', y=error_metric, 
                                      title=f'Minimum {error_metric} by time step', text='Model', color='Model Type')
    fig_min_errors_time_step.update_layout(plot_bgcolor='white', xaxis=dict(showgrid=True, gridcolor='lightgray'), 
                                           yaxis=dict(showgrid=True, gridcolor='lightgray'))
    fig_min_errors_time_step.show()

    data_agg = all_errors_per_time_step.groupby('Model').agg({
        'RMSE': 'mean', 'SMAPE': 'mean', 'RMSSE': 'mean', 'SMPE': 'mean',
        'ME': 'mean', 'MAE': 'mean', 'MASE': 'mean',
        'train_time': 'sum', 'avg_train_time': 'mean', 'Model Type': 'first'
    }).reset_index()
    
    data_agg_std = all_errors_per_time_step.groupby('Model').agg({
        'RMSE': 'std', 'SMAPE': 'std', 'RMSSE': 'std', 'SMPE': 'std',
        'ME': 'std', 'MAE': 'std', 'MASE': 'std'
    }).reset_index()
    
    data_agg = pd.merge(data_agg, data_agg_std, on='Model', suffixes=('', '_std'))

    best_models = data_agg.loc[data_agg.groupby('Model')[error_metric].idxmin()]

    fig_min_errors = create_sorted_bar_plot(best_models, 'Model', error_metric, 
                                            f'Minimum {error_metric} Total', 'Model Type', 'Model')
    fig_min_errors.show()
    
    fig_min_bias = create_sorted_bar_plot(best_models, 'Model', bias_metric, 
                                          f'Minimum {bias_metric} Total', 'Model Type', 'Model',sort_by_abs=True)
    fig_min_bias.show()

    fig_train_times = create_sorted_bar_plot(data_agg, 'Model', 'train_time', 
                                             'Total Training Times by Model Total', 'Model Type')
    fig_train_times.update_yaxes(type="log")
    fig_train_times.show()
    
    fig_train_times_avg = create_sorted_bar_plot(data_agg, 'Model', 'avg_train_time', 
                                                 'Avg Training Times by Model Total', 'Model Type')
    fig_train_times_avg.update_yaxes(type="log")
    fig_train_times_avg.show()
#######
    fig_box_plot_error = px.box(all_errors_per_time_step, x='Model', y=error_metric, 
                                title=f'Box Plot of {error_metric} by Model Sorted by Mean', color='Model Type')

    fig_box_plot_error.update_layout(plot_bgcolor='white', 
                                    xaxis=dict(showgrid=True, gridcolor='lightgray'), 
                                    yaxis=dict(showgrid=True, gridcolor='lightgray'))

    fig_box_plot_error.update_xaxes(categoryorder='mean ascending', 
                                    categoryarray=all_errors_per_time_step.groupby('Model')[error_metric].mean().sort_values().index)

    # Calculate and add mean value annotations
    mean_values = all_errors_per_time_step.groupby('Model')[error_metric].mean()
    for model in mean_values.index:
        fig_box_plot_error.add_annotation(
            x=model,
            y=all_errors_per_time_step[all_errors_per_time_step['Model'] == model][error_metric].max(),
            text=f"{mean_values[model]:.2f}",
            showarrow=False,
            # ax=0,
            # ay=-40,
            bordercolor="#c7c7c7",
            borderwidth=2,
            borderpad=4,
            # bgcolor="#ff7f0e",
            opacity=0.8,
            yshift = 19,
            font=dict(size=10)
        )

    fig_box_plot_error.show()
 ########   
    
    fig_box_plot_bias = px.box(all_errors_per_time_step, x='Model', y=bias_metric, title=f'Box Plot of {bias_metric} by Model', color='Model Type')
    fig_box_plot_bias.update_layout(
    plot_bgcolor='white', 
    xaxis=dict(showgrid=True, gridcolor='lightgray'), 
    yaxis=dict(showgrid=True, gridcolor='lightgray'))
    sorted_models = abs(all_errors_per_time_step.groupby('Model')[bias_metric].mean()).sort_values().index
    fig_box_plot_bias.update_xaxes( categoryorder='array', categoryarray=sorted_models)
    fig_box_plot_bias.show()

    naive_performance = data_agg[data_agg.Model == 'SeasonalNaive'][error_metric].values  
    fig_scatter = create_scatter_plot(data_agg, error_metric, naive_performance, f'Train Time vs {error_metric}')
    fig_scatter.show()

def plot_metric(error_metric, bias_metric, error_df, short_time_step_range=[1, 4], medium_time_step_range=[5, 12], long_time_step_range=[13, 18]):
    print(f'Plotting Error Metric: {error_metric}')
    print(f'Plotting Bias Metric: {bias_metric}')
    
    create_aggregated_plots_total(error_metric, bias_metric, error_df)
    create_aggregated_plots(error_metric, bias_metric, error_df, short_time_step_range, medium_time_step_range, long_time_step_range)

# Usage
plot_metric('RMSSE', 'SMPE', all_errors_per_time_step_accidental_deaths, short_time_step_range=[1, 4], medium_time_step_range=[5, 12], long_time_step_range=[13, 18])

In [ ]:
import plotly.graph_objs as go
import plotly.express as px

def plot_all_forecasts_errors_horizon(df_model):
    fig = go.Figure()
    
    # Print unique values in 'Model Type' column for debugging
    # print("Unique values in 'Model Type' column:", df_model['Model Type'].unique())
    # Generate a color for each unique model type
    unique_model_types = df_model['Model Type'].unique()
    colors = px.colors.qualitative.Plotly[:len(unique_model_types)]
    color_map = dict(zip(unique_model_types, colors))
    
    # Print color_map for debugging
    # print("Color map:", color_map)
    # Add forecasts with labels on the last point of each line
    for model in df_model['Model'].unique():
        df = df_model[df_model['Model'] == model]
        metric = 'RMSSE'
        model_type = df['Model Type'].iloc[0]  # Get the Model Type for this model
        
        # Display the label only on the last point
        fig.add_trace(go.Scatter(
            x=df['T+x'],
            y=df[metric],
            mode='lines+text',
            name=f'{model}',
            text=[None] * (len(df) - 1) + [f'{model}'],  # Label only the last point
            textposition='top right',  # Position the text label
            line=dict(color=color_map[model_type])  # Set the color based on Model Type
        ))
    
    fig.update_layout(title=f'Model Error for Time Step', xaxis_title='Horizon', yaxis_title=metric)
    fig.update_layout(
        width=1600,
        height=800,
    )
    fig.show()

# Call the function with your DataFrame
plot_all_forecasts_errors_horizon(all_errors_per_time_step_accidental_deaths)